# Toxic Spans Detection

In [45]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import ast
from termcolor import colored
import string
from nltk.tokenize import word_tokenize 
from tqdm import trange

![title](pipeline.jpeg)

- [1. Exploración](#1)
  - [1.1 Mal etiquetados](#1.1)
- [2. Preprocesamiento](#2)
- [3. Modelos](#3)
  - [3.1 Hidden Markov Model](#3.1)
  - [3.2 Conditional Random Fields for Sequence Prediction](#3.2)
  - [3.3 LSTM](#3.3)

<a name = "1"></a>
# Exploración

In [2]:
from utils import color_toxic_words

In [3]:
train = pd.read_csv('Datos/tsd_train.csv', converters={'spans':ast.literal_eval})
test = pd.read_csv('Datos/tsd_trial.csv', converters={'spans':ast.literal_eval})

In [4]:
train.head()

spans  \
0  [8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19,...   
1                       [33, 34, 35, 36, 37, 38, 39]   
2                                       [0, 1, 2, 3]   
3          [7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17]   
4                       [32, 33, 34, 35, 36, 37, 38]   

                                                text  
0  Another violent and aggressive immigrant killi...  
1  I am 56 years old, I am not your fucking junio...  
2                  Damn, a whole family. Sad indeed.  
3  What a knucklehead. How can anyone not know th...  
4  "who do you think should do the killing?"\n\nA...

Veamos las secciones tóxicas de algunas oraciones:

In [5]:
for i,(index,text) in enumerate(train.values[0:5]):
    print('{} - '.format(i) + color_toxic_words(index, text) + '\n'*2)

0 - Another violent and aggressive immigrant killing a innocent and intelligent US Citizen.... Sarcasm


1 - I am 56 years old, I am not your fucking junior pal. What you are saying makes no sense. I don't know what you are basing this on. The cheap black market crap is still coming up from Mexican nationals, and the good stuff from BC and Humbolt.  The I5 corridor is still just as busy, and they are still making a ton of money. Nothing has really changed except that the legal market has made it easy for anyone of legal age to buy it.  And the legal market is controlled by corporate growers with million dollar facilities, or a co-op of smaller growers. The Federal government "war on drugs" really has no impact on the legal market in Oregon. I don't see any glutton of weed, whatever that means.


2 - Damn, a whole family. Sad indeed.


3 - What a knucklehead. How can anyone not know this would be offensive??


4 - "who do you think should do the killing?"

Anyone and everyone. This is a

<a name = "1.1"></a>
### ¿Mal etiquetados?

En algunas oraciones pone los espacios, comas y otros signos como caracteres tóxicos, hay que tener cuidado y al final concatenarlos si es que hay dos o más palabras tóxicas juntas. En la competencia paracen concatenarlos, pero no son consistententes en otras partes.

In [6]:
very_toxic = [i for i,x in zip(train.index, train['spans']) if len(x)>100][0:5]

for i,(index,text) in zip(very_toxic, train.values[very_toxic]):
    print('{} - '.format(i) + color_toxic_words(index, text) + '\n'*2)

158 - These idiotic studies are upsetting. Where is the information that is surprising. Any person in any walk of like could and would state these (study) results?


159 - [To say that juxtaposing and making the same a massacre and overtly implying that someone had something to do with that massacre is mere "negligence" is absolutely asinine]
You confer what is determined based upon the evidence is "extremely silly or stupid?"  Is that how you see federal courts and judges function?
[Those "journalists" knew one thing had nothing to do with the other]
What are you waiting for?  You better call Palin and tell her you have evidence that proves the "journalists" knew that the two were not connected because that'll prove there was actual malice.
Wait.  Why don't I hear you dialing?
[Your unrelated SCOTUS case is cute]
Let me get this straight.  The judge in this article used exactly the standard but you deem it as "unrelated?"
You sir, are in complete and completely irrational denial.  It 

Y hay otros que definitivamente están mal etiquetados, donde no ponen lenguaje tóxico donde realmente sí lo hay.

In [7]:
actually_toxic = [27, 60, 82, 134, 382]

for index,text in train.values[actually_toxic]:
    print(color_toxic_words(index, text) + '\n'*2)

The malignant narcissist, mentally deranged sociopath, bigot, rascist, disingenuous blowhard and pathological liar, has now certified himself as a fascist. How much longer before his GOP sycophants and suckees say, "Enough!", and demand this repugnant, excrement-spewing fool's ouster?


the is NO CONSENSUS you ignorant loser, NONE, nothing but debate, thousands of scientist do not agree period, we dont need to move from anything other than left wing stupidity like yours.


aa nadda showing the usual stupidity, its clowns like you that live outside reality, see pal canada needs the usa, the usa does not need us. , dont get me wrong, trudeau an ignorant child with no leadership skills doing real damage to canada with bs like carbon taxes...


Try reading my entire comment again, except slower, and then take a few moments for reflection, days if need be. If by then you still don't understand that the Trumpster is Putins bitch, you'll never get it.


You are just a stick buthole!




<a name = "2"></a>
## Preprocesamiento
Primero sería mejor tener las palabras tóxicas que los caracteres, también hay que tener cuidado cuando marcan un espacio o algún signo de puntuación como tóxico, al final sólo hay que concatenar si hay dos palabras tóxicas juntas (por hacer). También hay que pasar todo a minúscula y hacer el análisis en minúscula.

In [8]:
import string
from utils import remove_symbols

In [9]:
text = 'fuck you idiot!!!'
index = np.arange(len(text)).tolist()

print(color_toxic_words(index, text))
print(color_toxic_words(remove_symbols(index, text), text))

fuck you idiot!!!
fuck you idiot!!!


In [10]:
indices_clean = [remove_symbols(index, text) for index,text in 
                 zip(train['spans'], train['text'])]

train['spans_clean'] = indices_clean

Veamos como se ven si lo hacemos así:

In [11]:
very_toxic = [i for i,x in zip(train.index, train['spans']) if len(x)>100][0:3]

for i, (index,text,index_clean) in zip(very_toxic, train.values[very_toxic]):
    print('{} - '.format(i) + color_toxic_words(index, text))
    print('{} - '.format(i) + color_toxic_words(index_clean, text) + '\n'*2)

158 - These idiotic studies are upsetting. Where is the information that is surprising. Any person in any walk of like could and would state these (study) results?
158 - These idiotic studies are upsetting. Where is the information that is surprising. Any person in any walk of like could and would state these (study) results?


159 - [To say that juxtaposing and making the same a massacre and overtly implying that someone had something to do with that massacre is mere "negligence" is absolutely asinine]
You confer what is determined based upon the evidence is "extremely silly or stupid?"  Is that how you see federal courts and judges function?
[Those "journalists" knew one thing had nothing to do with the other]
What are you waiting for?  You better call Palin and tell her you have evidence that proves the "journalists" knew that the two were not connected because that'll prove there was actual malice.
Wait.  Why don't I hear you dialing?
[Your unrelated SCOTUS case is cute]
Let me get

También pasemos a minúscula el texto para el entrenamiento:

In [12]:
train['text'] = train['text'].apply(lambda x:x.lower())

<a name = "3"></a>
## Modelos

En la competencia usarán el F1 score para evaluar como sigue:

<blockquote cite="http://www.worldwildlife.org/who/index.html">
To evaluate the responses of a system participating in the challenge, we employ the $F_{1}$ score, as in [1]. Let system $A_i$ return a set $S^{t}_{A_{i}}$ of character offsets, for parts of the post found to be toxic. Let $G^{t}$ be the character offsets of the ground truth annotations of $t$. We compute the $F_{1}$ score of system $A_i$ with respect to the ground truth $G$ for post $t$ as follows, where $|·|$ denotes set cardinality.
    
$$ F_{1}^{t}(A_{i}, G) = \dfrac{2 \cdot P^{t}(A_{i}, G) \cdot R^{t}(A_{i}, G)}{P^{t}(A_{i}, G) + R^{t}(A_{i}, G)}$$
    
$$ P^{t}(A_{i}, G) = \dfrac{|S^{t}_{A_{i}} \cap S^{t}_{A_{i}}|}{|S^{t}_{A_{i}}|} $$
    
$$ R^{t}(A_{i}, G) = \dfrac{|S^{t}_{A_{i}} \cap S^{t}_{A_{i}}|}{|S^{t}_{G}|} $$    
    
If $S^{t}_{G}$ is empty for some post $t$ (no gold spans are given for $t$), we set $F_{1}^{t}(A_{i}, G)$ if $S^{t}_{A_{i}}$ is also empty, and $F_{1}^{t}(A_{i}, G) = 0$ otherwise. We finally average $F_{1}^{t}(A_{i}, G)$ over all the posts $t$ of an evaluation dataset $T$ to obtain a single score for system $A_{i}$.

</blockquote>

In [13]:
from utils import separate_words, get_index_toxic_words

In [14]:
# La siguiente función viene en el GitHub de la competencia.
def f1(predictions, gold):
    """
    F1 (a.k.a. DICE) operating on two lists of offsets (e.g., character).
    >>> assert f1([0, 1, 4, 5], [0, 1, 6]) == 0.5714285714285714
    :param predictions: a list of predicted offsets
    :param gold: a list of offsets serving as the ground truth
    :return: a score between 0 and 1
    """
    if len(gold) == 0:
        return 1. if len(predictions) == 0 else 0.
    if len(predictions) == 0:
        return 0.
    predictions_set = set(predictions)
    gold_set = set(gold)
    nom = 2 * len(predictions_set.intersection(gold_set))
    denom = len(predictions_set) + len(gold_set)
    return float(nom)/float(denom)

<a name = "3.1"></a>
### Hidden Markov Model

In [15]:
import nltk
from nltk.corpus import treebank
from nltk.tag import HiddenMarkovModelTrainer
from nltk.tokenize import word_tokenize

En nuestro caso debemos etiquetar en `toxic` y `non_toxic`.

In [16]:
train_data = []
for index, text in zip(train['spans_clean'], train['text']):
    toxic_words = [text[i[0]:i[-1]+1] for i in separate_words(index) if len(index) > 0]
#     print(toxic_words)
    
    tokens = word_tokenize(text)
    tagged_tokens = []
    
    for token in tokens:
        if token in toxic_words:
            tagged_tokens.append((token, 'toxic'))
            # Removemos en caso de que se repita posteriormente pero esté como 'non_toxic'
            toxic_words.remove(token) 
        else:
            tagged_tokens.append((token, 'non_toxic'))
            
    train_data.append(tagged_tokens)

Entrenamos:

In [17]:
trainer = HiddenMarkovModelTrainer()
tagger_HMM = trainer.train_supervised(train_data)

Ahora hagamos algunos experimentos:

In [18]:
text = 'fucking piece of shit, suck my dick'
tagged_sentence = tagger_HMM.tag(word_tokenize(text))
toxic_index = get_index_toxic_words(text, tagged_sentence)

print(tagged_sentence)
print(color_toxic_words(toxic_index, text))

[('fucking', 'toxic'), ('piece', 'toxic'), ('of', 'toxic'), ('shit', 'toxic'), (',', 'non_toxic'), ('suck', 'toxic'), ('my', 'toxic'), ('dick', 'toxic')]
fucking piece of shit, suck my dick


In [19]:
text = 'have a nice day, my dear nigger'
tagged_sentence = tagger_HMM.tag(word_tokenize(text))
toxic_index = get_index_toxic_words(text, tagged_sentence)

print(tagged_sentence)
print(color_toxic_words(toxic_index, text))

[('have', 'non_toxic'), ('a', 'non_toxic'), ('nice', 'non_toxic'), ('day', 'non_toxic'), (',', 'non_toxic'), ('my', 'non_toxic'), ('dear', 'non_toxic'), ('nigger', 'toxic')]
have a nice day, my dear nigger


Veamos que score tenemos en el dataset de `test` y comparemos nuestras predicciones:

In [20]:
scores_HMM = []

for gold_index, text in test.values:
    tagged_sentence = tagger_HMM.tag(word_tokenize(text.lower()))   
    prediction_index = get_index_toxic_words(text.lower(), tagged_sentence)
    
    print(colored('Pred: ', color='cyan', attrs=['bold']) + 
          color_toxic_words(prediction_index, text))   
    print(colored('Gold: ', color='yellow', attrs=['bold']) + 
          color_toxic_words(gold_index, text) + '\n'*2)
    
    scores_HMM.append(f1(prediction_index, gold_index))

Pred: Because he's a moron and a bigot. It's not any more complicated than that.
Gold: Because he's a moron and a bigot. It's not any more complicated than that.


Pred: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.
Gold: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.


Pred: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...
Gold: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...


Pred: Trump Claimed that Russia will never invade the Ukraine, when Russia already has - how stupid can people be?
Gold: Trump Claimed that Russia w

Pred: That's contradicted by the facts. First of all, Democrats have acknowledged the past and the party evolved to the anti-racist side, which prompted southern racists who used to constitute the Solid South for the party to migrate to the GOP, where the South now pretty much votes solidly for Republicans due to the GOP's adoption of the racist polices the Democrats used to push. If there are any remaining racists in the Democratic Party, the members will marginalize and push them out.

The Democratic Party of the 1800s, though, was the conservative party. They were not "leftist" at all.

Entitlements are not "slavery." That's just a silly remark, pre-packaged propaganda to demonize people who need help. Look at Ben Carson -- on public assistance and loans and public housing all his life until he made it on his own, and now he demonizes welfare. Bunch of hypocrites.
Gold: That's contradicted by the facts. First of all, Democrats have acknowledged the past and the party evolved to the 

Pred: Like I said you can't grasp it. We have to put up with intolerant people here because  they were born here. Is it that hard of a concept. We do not let in those who are intolerant and give them Canadian rights. Your kids will have zero tolerance until your kids grow up and start living in the real world, start paying exhorbitant taxes, exhorbitant prices for homes, food, water, bills, etc. Doesn't mean they'll be racist. Just means they'll learn about debts and how we cannot afford to help every poor soul. It is a numbers game and if you haven't noticed our number is at a trillion and Liberals have been projected at an added 1.5 trillion of debt.  Wake your dumb a$$ up. I studied the charter in school way back when and knew it was for CANADIANS not immigrants.
Gold: Like I said you can't grasp it. We have to put up with intolerant people here because  they were born here. Is it that hard of a concept. We do not let in those who are intolerant and give them Canadian rights. Your k

Pred: I think Americans believe their president should be free to speak to whoever he thinks best.

So PRC can go suck eggs.
Gold: I think Americans believe their president should be free to speak to whoever he thinks best.

So PRC can go suck eggs.


Pred: You fool. The NEP had nothing to do with world oil  prices dropping to 5 bucks a barrel. 
You must have spent your Ralph bucks.
Gold: You fool. The NEP had nothing to do with world oil  prices dropping to 5 bucks a barrel. 
You must have spent your Ralph bucks.


Pred: A hell of a lot more than republicans have to show.  Hell the idiots couldn't even replace Obama care, something they have run against for the past 7 years.  When the economy crashes, it will be interesting to see just what the hell republicans will do?  Anything?
Gold: A hell of a lot more than republicans have to show.  Hell the idiots couldn't even replace Obama care, something they have run against for the past 7 years.  When the economy crashes, it will be intere

Pred: Monsef is an idiot and should be turfed from the Cabinet ....but Comrade Sunny Days is too enamoured with her....
Gold: Monsef is an idiot and should be turfed from the Cabinet ....but Comrade Sunny Days is too enamoured with her....


Pred: Democrat message: TRUMP IS A BAD GUY. . ..Elect us!
Gold: Democrat message: TRUMP IS A BAD GUY. . ..Elect us!


Pred: had this happened, had that happened.... so what - how stupid.  He'll never catch Gretzky
Gold: had this happened, had that happened.... so what - how stupid.  He'll never catch Gretzky


Pred: Never uttered or wrote that crap. You're a liar stuck in a pig fight with yourself. Don't forget the lipstick.
Gold: Never uttered or wrote that crap. You're a liar stuck in a pig fight with yourself. Don't forget the lipstick.


Pred: Trump is the biggest hypocrite and pathological liar the Republicans have produced yet, and conservatives lap up his lies like the sheep they are.
Gold: Trump is the biggest hypocrite and pathological lia

Pred: Your not understaning grammer, fool. Your a Leftie poster with no comon senze.
Gold: Your not understaning grammer, fool. Your a Leftie poster with no comon senze.


Pred: Thanks to Donald Trump and his equally clueless Republican politicians for helping bring this amazing convention to Denver! I feel sorry for the folks of Utah who are against Trump's ignorant policies, but if it takes situations like this for the country to realize what a buffoon Donald Trump and some of his fellow Republicans are, then maybe the country will step up the efforts to get Trump impeached. He is completely unfit to run our country, and this is just one of his amazingly ignorant decisions. He's mentally unfit and everything he does is to pad his own bank account. What a joke!
Gold: Thanks to Donald Trump and his equally clueless Republican politicians for helping bring this amazing convention to Denver! I feel sorry for the folks of Utah who are against Trump's ignorant policies, but if it takes sit

Gold: Trump is a disgusting pig. I am ashamed that he is president.


Pred: Kill all the nigggers and pedophiles!
Gold: Kill all the nigggers and pedophiles!


Pred: If the pedestrians are too stupid, too arrogant, too self-absorbed in themselves or their cell phones or their companions to use the devices designed to keep them alive with minimal effort, I don't have any sympathy for them whatsoever.

I will have sympathy for the person who couldn't avoid them, just like the young man who couldn't avoid the 'impaired' guy on the bicycle after dark with no lights.  The first driver missed him, the second couldn't.  

The driver in this instance deserves sympathy; the bicyclist....

Your idiots who can't push a little button.....the same as the bicyclist.
Gold: If the pedestrians are too stupid, too arrogant, too self-absorbed in themselves or their cell phones or their companions to use the devices designed to keep them alive with minimal effort, I don't have any sympathy for them whatso

Pred: Who is the stupid head who built a rock wall to enclose the boat dock across the street from the Oahu Club. That was supposed to be left open so floods can drain naturally. Now this will cause delayed drainage and more flooding to wider areas. Destroy it now!
Gold: Who is the stupid head who built a rock wall to enclose the boat dock across the street from the Oahu Club. That was supposed to be left open so floods can drain naturally. Now this will cause delayed drainage and more flooding to wider areas. Destroy it now!


Pred: "Or perhaps it would be more expedient for the commission to throw such letters in the trash themselves, and save the bishops' staffs the trouble."

I think this was the original plan, but Francis could not get Muller's permission for this because it violated the principle of stupidiarity.
Gold: "Or perhaps it would be more expedient for the commission to throw such letters in the trash themselves, and save the bishops' staffs the trouble."

I think this w

In [21]:
print('HMM score: {:.3f}'.format(np.mean(scores_HMM)))

HMM score: 0.321


<a name = "3.2"></a>
### Conditional Random Fields for Sequence Prediction

In [22]:
from itertools import chain
from nltk import pos_tag
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.preprocessing import LabelBinarizer
import sklearn
import pycrfsuite
from tqdm import tqdm
from utils import word2features, sent2features, sent2labels, sent2tokens, token_postag_label

In [23]:
train_data_crf = []
for text, toxic_tags in tqdm(zip(train['text'], train_data), total=len(train_data)):
    pos_tags = token_postag_label(text.lower())
    sentence = []
    for x,y in zip(pos_tags, toxic_tags):
        sentence.append(x + (y[1],))
        
    train_data_crf.append(sentence)

100%|██████████| 7939/7939 [00:09<00:00, 812.50it/s]


In [24]:
X_train = [sent2features(s) for s in train_data_crf]
y_train = [sent2labels(s) for s in train_data_crf]

trainer = pycrfsuite.Trainer(verbose=False)

for xseq, yseq in zip(X_train, y_train):
    trainer.append(xseq, yseq)

Probablemente sea buena idea hacer una búsqueda de los mejores hiperparámetros, ya que el performance cambia significativamente dependiendo de los hiperparámetros.

In [27]:
trainer.set_params({
    'c1': 1.0,   # coefficient for L1 penalty
    'c2': 0.01,  # coefficient for L2 penalty
    'max_iterations': 100,  # stop earlier
    # include transitions that are possible, but not observed
    'feature.possible_transitions': True
})

# trainer.params()

In [31]:
%time trainer.train('toxic_speech.crfsuite')

tagger_crf = pycrfsuite.Tagger()
tagger_crf.open('toxic_speech.crfsuite')

CPU times: user 11.8 s, sys: 3.23 ms, total: 11.8 s
Wall time: 11.8 s


In [29]:
test_data_crf =  []
for text in tqdm(test['text']):
    pos_tags = token_postag_label(text.lower())
    sentence = []
    for x in pos_tags:
        sentence.append(x + ('',))
        
    test_data_crf.append(sentence)

100%|██████████| 690/690 [00:00<00:00, 875.49it/s]


In [32]:
scores_CRF = []

for text_crf,(gold_index,text) in zip(test_data_crf, test.values):
    words = [x[0] for x in text_crf]
    tags = tagger_crf.tag(sent2features(text_crf))
    
    tagged_sentence = [(word, tag) for word,tag in zip(words,tags)]
    prediction_index = get_index_toxic_words(text.lower(), tagged_sentence)
    
    print(colored('Pred: ', color='cyan', attrs=['bold']) + 
          color_toxic_words(prediction_index, text))   
    print(colored('Gold: ', color='yellow', attrs=['bold']) + 
          color_toxic_words(gold_index, text) + '\n'*2)
    
    scores_CRF.append(f1(prediction_index, gold_index))

Pred: Because he's a moron and a bigot. It's not any more complicated than that.
Gold: Because he's a moron and a bigot. It's not any more complicated than that.


Pred: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.
Gold: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.


Pred: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...
Gold: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...


Pred: Trump Claimed that Russia will never invade the Ukraine, when Russia already has - how stupid can people be?
Gold: Trump Claimed that Russia w

Gold: Awful comment


Pred: When will natives clean up their act and stop using the creations of whiteman?   They don't think they have to. They think it is their moral right to tell us everything they don't like about us.   Until they give up  tshirts,  jeans, pizza, cars, trucks and beer they are  nations of hypocrites.
Gold: When will natives clean up their act and stop using the creations of whiteman?   They don't think they have to. They think it is their moral right to tell us everything they don't like about us.   Until they give up  tshirts,  jeans, pizza, cars, trucks and beer they are  nations of hypocrites.


Pred: These union as---oles don't care about the animals -why are they unionized anyways....th job requires zero educaton, much like most public jobs - the animals are muchsmarterthan these 400 morons
Gold: These union as---oles don't care about the animals -why are they unionized anyways....th job requires zero educaton, much like most public jobs - the animals are muc

Gold: Talkeetna has never had any problem with Marijuana. I say "Open a pot shop the size of walmart and tell those soccer moms to kiss your butt." It's a free country and pot is legal. Hey soccer moms,go fight something serious like meth.


Pred: You are an ignorant A hole
Gold: You are an ignorant A hole


Pred: with all the ignorant left wingers here perhaps we can get them some help with thier stupidity
Gold: with all the ignorant left wingers here perhaps we can get them some help with thier stupidity


Pred: Putin is a murdering kleptocrat dictator, and you are a fool.
Gold: Putin is a murdering kleptocrat dictator, and you are a fool.


Pred: Hopefully we still have NATO allies given the rhetoric of the idiot we have in the White House.
Gold: Hopefully we still have NATO allies given the rhetoric of the idiot we have in the White House.


Pred: 907:  You are a foolish troll with absolutely no credibility.  Keep that in mind.
Gold: 907:  You are a foolish troll with absolutely no

Pred: He should have died in Afghanistan and be with Satan now--but we are stuck with this deviant killer.
Gold: He should have died in Afghanistan and be with Satan now--but we are stuck with this deviant killer.


Pred: Laughable.   The great negotiator  can't keep employees and has backtracked on his promises repeatedly. His negotiating skills are all based on bullying .Hows that working in congress?  We need to unite against the moron and save our country. 
Bigly Sad
Gold: Laughable.   The great negotiator  can't keep employees and has backtracked on his promises repeatedly. His negotiating skills are all based on bullying .Hows that working in congress?  We need to unite against the moron and save our country. 
Bigly Sad


Pred: rr,I dsagree with you proposal as being ludicrous.  okay?
Gold: rr,I dsagree with you proposal as being ludicrous.  okay?


Pred: The president is obviously mentally ill.  This is not how a 71 year old man acts - ever.  Even his worshipers are finally - at

Gold: Lol really. No offence but that’s an idiotic statement. I’m not looking for likes from the douches on the left/ right political side of things. You can’t honestly think this though. Our government federally and provincially across Canada works exactly like this. The more money in the more money spent. It is always, and will always be spent with little oversight, common sense, little efficiency. That’s it. You see provinces with hst taxing more that have massive debts. Obviously more money didn’t make them better money managers, quite the opposite actually. They post phony  surpluses but debts are ever increasing. The problem is the way money is spent. That’s it. Bloated public sectors that’s sole obligation is to become more bloated. What bloats more then more money. Don’t be naive to think less equalization would magically turn these inept politicians to manage money any better. That includes cons, libs, and dippers. They have zero sense of money management and probably never wi

Gold: You wouldn't know truth if it came up and smack you on the  butt.


Pred: The only morons I see hear are those who rated your comment as "civil".
Gold: The only morons I see hear are those who rated your comment as "civil".


Pred: In realty, Jeff Stober  is  very cruel, self serving, and nasty to say the least. He just acts like he's a good person because it benefits his company's profit margin. If someone wrote the actual truth about him, everyone would be appalled.
Gold: In realty, Jeff Stober  is  very cruel, self serving, and nasty to say the least. He just acts like he's a good person because it benefits his company's profit margin. If someone wrote the actual truth about him, everyone would be appalled.


Pred: SO MUCH WINNING BY NIKKI HALEY - she's going to make a great first woman president (sorry Hillary but no one likes you but everyone likes Nikki Haley, plus she's way better looking and not a lesbian :o
Gold: SO MUCH WINNING BY NIKKI HALEY - she's going to make a gre

Pred: You are a moron.  Learn to read.
Gold: You are a moron.  Learn to read.


Pred: Thanks for hating, coward.
Gold: Thanks for hating, coward.


Pred: I don't respond to dumb rhetorical questions.
Gold: I don't respond to dumb rhetorical questions.


Pred: Nevermind Karen I know who the fuck u r how dare u speak on some shit u don't know about u'll be hearing from me in the morning
Gold: Nevermind Karen I know who the fuck u r how dare u speak on some shit u don't know about u'll be hearing from me in the morning


Pred: Ridiculous logic!

G&M sure seem hooked to Real Estate industry cash (propaganda pieces in exchange of ad cash), Trudeau and paying interest on massive Federal debt.
Gold: Ridiculous logic!

G&M sure seem hooked to Real Estate industry cash (propaganda pieces in exchange of ad cash), Trudeau and paying interest on massive Federal debt.


Pred: Uh, no.
Millennial are lazy, dodgy (when it comes to work-work, school-work they do alright) and dumb.
They are brainwashed 

In [33]:
print('CRF score: {:.3f}'.format(np.mean(scores_CRF)))

CRF score: 0.551


<a name = "3.3"></a>
### LSTM

In [38]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

torch.manual_seed(1)
torch.cuda.current_device(), torch.cuda.get_device_name(0)

(0, 'GeForce RTX 2070')

In [39]:
train_data = []
for index, text in zip(train['spans_clean'], train['text']):
    toxic_words = [text[i[0]:i[-1]+1] for i in separate_words(index) if len(index) > 0]
#     print(toxic_words)
    
    tokens = word_tokenize(text)
    tagged_tokens = []
    
    for token in tokens:
        if token in toxic_words:
            tagged_tokens.append('toxic')
            # Removemos en caso de que se repita posteriormente pero esté como 'non_toxic'
            toxic_words.remove(token) 
        else:
            tagged_tokens.append('non_toxic')
            
    train_data.append((tokens, tagged_tokens))

In [40]:
def prepare_sequence(seq, to_ix):
    idxs = [to_ix.get(w, 0) for w in seq]      # Si no está que lo ponga como 'UNK'
    return torch.tensor(idxs, dtype=torch.long)

In [41]:
word_to_ix = {'UNK': 0}

for sent, tags in train_data:
    for word in sent:
        if word not in word_to_ix:  # word has not been assigned an index yet
            word_to_ix[word] = len(word_to_ix)  # Assign each word with a unique index
            
tag_to_ix = {"non_toxic": 0, "toxic": 1}  # Assign each tag with a unique index

Creamos el modelo:

In [42]:
class LSTMTagger(nn.Module):

    def __init__(self, embedding_dim, hidden_dim, vocab_size, tagset_size):
        super(LSTMTagger, self).__init__()
        self.hidden_dim = hidden_dim

        self.word_embeddings = nn.Embedding(vocab_size, embedding_dim)

        # The LSTM takes word embeddings as inputs, and outputs hidden states
        # with dimensionality hidden_dim.
        self.lstm = nn.LSTM(embedding_dim, hidden_dim)

        # The linear layer that maps from hidden state space to tag space
        self.hidden2tag = nn.Linear(hidden_dim, tagset_size)

    def forward(self, sentence):
        embeds = self.word_embeddings(sentence)
        lstm_out, _ = self.lstm(embeds.view(len(sentence), 1, -1))
        tag_space = self.hidden2tag(lstm_out.view(len(sentence), -1))
        tag_scores = F.log_softmax(tag_space, dim=1)
        return tag_scores

Entrenamos el modelo:

In [43]:
# These will usually be more like 32 or 64 dimensional.
EMBEDDING_DIM = 32
HIDDEN_DIM = 32

model = LSTMTagger(EMBEDDING_DIM, HIDDEN_DIM, len(word_to_ix), len(tag_to_ix))
loss_function = nn.NLLLoss()
optimizer = optim.SGD(model.parameters(), lr=0.1)

In [44]:
with torch.no_grad():
    inputs = prepare_sequence(train_data[0][0], word_to_ix)
    tag_scores = model(inputs)
#     print(tag_scores)
    
for epoch in trange(10):  
    for sentence, tags in train_data:
        # Step 1. Remember that Pytorch accumulates gradients.
        # We need to clear them out before each instance
        model.zero_grad()

        # Step 2. Get our inputs ready for the network, that is, turn them into
        # Tensors of word indices.
        sentence_in = prepare_sequence(sentence, word_to_ix)
        targets = prepare_sequence(tags, tag_to_ix)

        # Step 3. Run our forward pass.
        tag_scores = model(sentence_in)

        # Step 4. Compute the loss, gradients, and update the parameters by
        #  calling optimizer.step()
        loss = loss_function(tag_scores, targets)
        loss.backward()
        optimizer.step()

100%|██████████| 10/10 [07:08<00:00, 42.87s/it]


In [46]:
def tagger_LSTM(text):
    ix_to_tag = {0: 'non_toxic', 1: 'toxic'}
    words = word_tokenize(text.lower())
    
    with torch.no_grad():
        inputs = prepare_sequence(words, word_to_ix)
        tag_scores = model(inputs)
        tags = [np.argmax(x.numpy()) for x in tag_scores]

        tagged_sentence = [(word, ix_to_tag[tag]) for word,tag in zip(words, tags)]

    return tagged_sentence

In [47]:
scores_LSTM = []

for gold_index, text in test.values:
    tagged_sentence = tagger_LSTM(text)   
    prediction_index = get_index_toxic_words(text.lower(), tagged_sentence)
    
    print(colored('Pred: ', color='cyan', attrs=['bold']) + 
          color_toxic_words(prediction_index, text))   
    print(colored('Gold: ', color='yellow', attrs=['bold']) + 
          color_toxic_words(gold_index, text) + '\n'*2)
    
    scores_LSTM.append(f1(prediction_index, gold_index))
    

Pred: Because he's a moron and a bigot. It's not any more complicated than that.
Gold: Because he's a moron and a bigot. It's not any more complicated than that.


Pred: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.
Gold: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.


Pred: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...
Gold: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...


Pred: Trump Claimed that Russia will never invade the Ukraine, when Russia already has - how stupid can people be?
Gold: Trump Claimed that Russia w


Pred: There's a difference between saying the choice is a mistake and inferring a user is stupid. Nothing personal "friend".
Gold: There's a difference between saying the choice is a mistake and inferring a user is stupid. Nothing personal "friend".


Pred: Clinton lost because she's an unlikable incompetent hack who has  a long history of corruption, bribe-taking, lawbreaking, graft, greed, and who purposely handled classified documents on an illegal and vulnerable private server in her bathroom.  She didn't lose because of the Russians. She lost because of 30 years of lying, cheating, corrupt behavior and arrogant stupidity.
Gold: Clinton lost because she's an unlikable incompetent hack who has  a long history of corruption, bribe-taking, lawbreaking, graft, greed, and who purposely handled classified documents on an illegal and vulnerable private server in her bathroom.  She didn't lose because of the Russians. She lost because of 30 years of lying, cheating, corrupt behavior and a


Pred: I don't get it. What's wrong with having a lying, ignorant, unethical incompetent with the attention span and emotional immaturity of a child for president?
Gold: I don't get it. What's wrong with having a lying, ignorant, unethical incompetent with the attention span and emotional immaturity of a child for president?


Pred: Sometimes you have to burn the village in order to save it.
Gold: Sometimes you have to burn the village in order to save it.


Pred: This is absolutely disgusting. Of course this garbage has an attached emergency clause. Kate Brown and her liberal cronies who proposed this nonsense need to be deported along with all the damn illegals who they want to support with our money. Screw them!
Gold: This is absolutely disgusting. Of course this garbage has an attached emergency clause. Kate Brown and her liberal cronies who proposed this nonsense need to be deported along with all the damn illegals who they want to support with our money. Screw them!


Pred: But h

Pred: Mark Hume has always been the stereotypical Vancouverite. Scream how logging must be stopped, while living in a house made of wood. It's so far past hypocritical to be ridiculous.
Gold: Mark Hume has always been the stereotypical Vancouverite. Scream how logging must be stopped, while living in a house made of wood. It's so far past hypocritical to be ridiculous.


Pred: Every country that has 50% or over Muslims makes for other faiths or individuals very hard to live. Talking about being victim, how about thousands of Indian who were tortured and killed because they would not accept Islam. What about their identity. What about identity of countless Christians in Arabic countries : like Iraq, Syria, etc tortured and killed I totally horrific ways but Muslims what about their victimization, what about their rights. 
Those articles written about current situations in this newspaper are totally pathetic. It’s a joke.
Gold: Every country that has 50% or over Muslims makes for other f

Pred: Tell that to the Islamists who pray five times a day.  Tell that to the sex fiends who are teaching Grade 3 students homosexuality and gender identity  What kind of men and boys will these students be to women when they have no "SELF CONTROL".
Gold: Tell that to the Islamists who pray five times a day.  Tell that to the sex fiends who are teaching Grade 3 students homosexuality and gender identity  What kind of men and boys will these students be to women when they have no "SELF CONTROL".


Pred: Quit being a plethora of idiotic statements.
Gold: Quit being a plethora of idiotic statements.


Pred: These oil soaked clowns in the legislative majorities have drug this out for 5 months now and this is the best they can come up with. If I were Walker I'd plant their asses in Anchorage where the public can get to them for as long as it takes and for as many special sessions as it takes. They've already cost us millions and millions of dollars on garbage that we'll never see a dimes wo

Pred: The Anchorage Crime report this year said white women are raped in most cases by white men, not minority men.  
This is for you From Lisa Bloom. Lisa Bloom is a Legal analyst for NBC News and Avvo, attorney and bestselling author.

"In our nation’s history, so many of the sickest most appalling crimes have been committed by whites. Yet no matter how sadistic the crime, no matter how young the victims, no matter how much fear is engendered in a community, no matter how much media attention and public discussion the crimes of whites engender, the race itself is never sullied." 

Lisa Bloom also says white men are at the top of the list for gaining foreign visas to have sex with children. 85-percent in Latin America, she says.

Lisa Bloom also adds the most prolific serial killers in this country (America) are white men. And last, white women are known for killing their children. Any studies to back your gossip?

I am aware of truth. I'm an old cops and crime reporter from way back.

Pred: This bill is a tax cut disguised as a health care bill. People will die if this bill passes. To deny this fact is to bury your head even farther up Trumps ass. Makes me sick.
Gold: This bill is a tax cut disguised as a health care bill. People will die if this bill passes. To deny this fact is to bury your head even farther up Trumps ass. Makes me sick.


Pred: Sorry, but that has to be one of the most ignorant statements I've read.  Because you may not favor gender neutral bathrooms, you support rapist?  Good grief.
Gold: Sorry, but that has to be one of the most ignorant statements I've read.  Because you may not favor gender neutral bathrooms, you support rapist?  Good grief.


Pred: What in the heck are you talking about?  This has absolutely nothing to do with the government or Obama.  This is entirely a result of TSA's inability to adjust to modern spending habits.  Look how many Amazon boxes show up in your neighborhood everyday.  Your prejudice is unmistakeable and comple

Pred: Back pedaling coward. Clearly Murkowski would kill him.
Gold: Back pedaling coward. Clearly Murkowski would kill him.


Pred: Come on Motley, that's garbage. I expect better from you. So my question stands, did Romney get on his knees "under the dinner table", to presumably perform fellatio on Donald Trump? Really? Why bring that filth to this forum, whether true or not, and we all know it isn't true, it's just something vile that crept out of your brain.

Sorry, some days I can handle BS, other days, it just seems like trash from hell.
Gold: Come on Motley, that's garbage. I expect better from you. So my question stands, did Romney get on his knees "under the dinner table", to presumably perform fellatio on Donald Trump? Really? Why bring that filth to this forum, whether true or not, and we all know it isn't true, it's just something vile that crept out of your brain.

Sorry, some days I can handle BS, other days, it just seems like trash from hell.


Pred: The way some of you 

In [48]:
print('LSTM score: {:.3f}'.format(np.mean(scores_LSTM)))

LSTM score: 0.561
